In [1]:
%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [2]:
import warnings

warnings.simplefilter("ignore")

<div class="main-title">
<h1>SRAI</h1>
<p>Design and usage<p>
</div>

## What is SRAI?

<div class="center-content">
    <h3 style="margin: auto;">A toolbox for geospatial AI</h3>
</div>

<div class="center-content">
    <p style="margin: auto;">...that aims to standardize the domain</p>
</div>

<div>
    <img src="assets/SRAI-diagram.png" class="srai-diagram"/>
</div>

Specify the city

In [3]:
CITY = "Basel"
COUNTRY = "Switzerland"

area_name = f"{CITY}, {COUNTRY}"
area_name

'Basel, Switzerland'

Download the area

In [4]:
from srai.regionalizers import geocode_to_region_gdf

area = geocode_to_region_gdf(area_name)
area.explore(height=500)

## Loaders

* used to load spatial data from different sources
* unify loading into a single interface
* prepare data for the embedding methods

[API](https://kraina-ai.github.io/srai/latest/api/loaders/)<br>
[Examples](https://kraina-ai.github.io/srai/latest/examples/loaders/)

Types of loaders:

* GeoparquetLoader
* GTFSLoader
* OSMOnlineLoader
* OSMPbfLoader
* OSMWayLoader
* OSMTileLoader

### Let's create a city poster

In [5]:
from srai.loaders.osm_loaders.filters import BASE_OSM_GROUPS_FILTER

BASE_OSM_GROUPS_FILTER

{'water': {'natual': ['water', 'bay', 'beach', 'coastline'],
  'waterway': ['riverbank']},
 'aerialway': {'aerialway': ['cable_car',
   'gondola',
   'mixed_lift',
   'chair_lift',
   'drag_lift',
   't-bar',
   'j-bar',
   'platter',
   'rope_tow',
   'magic_carpet',
   'zip_line',
   'goods',
   'station']},
 'airports': {'aeroway': ['aerodrome', 'heliport', 'spaceport']},
 'sustenance': {'amenity': ['bar',
   'bbq',
   'biergarten',
   'cafe',
   'fast_food',
   'food_court',
   'ice_cream',
   'pub',
   'restaurant']},
 'education': {'amenity': ['college',
   'driving_school',
   'kindergarten',
   'language_school',
   'library',
   'toy_library',
   'music_school',
   'school',
   'university']},
 'transportation': {'amenity': ['bicycle_parking',
   'bicycle_repair_station',
   'bicycle_rental',
   'boat_rental',
   'boat_sharing',
   'car_rental',
   'car_sharing',
   'car_wash',
   'charging_station',
   'bus_stop',
   'ferry_terminal',
   'fuel',
   'motorcycle_parking',
   'p

In [6]:
from srai.loaders import OSMPbfLoader

features = (
    OSMPbfLoader()
    .load(area, {"highway": True, "water": True, "waterway": True})
    .clip(area)
)
features.head(3)

[Basel, Basel-City, Switzerland] Counting pbf features: 636273it [00:01, 322177.02it/s]
[Basel, Basel-City, Switzerland] Parsing pbf file #1: 100%|██████████| 636273/636273 [00:07<00:00, 82993.72it/s] 


geometry      highway  \
feature_id                                                                      
way/26623782   LINESTRING (7.58962 47.52428, 7.58958 47.52412...        track   
way/23979464     LINESTRING (7.58962 47.52428, 7.58957 47.52428)      footway   
way/290406242  LINESTRING (7.58964 47.52433, 7.59045 47.52434...  residential   

              water waterway  
feature_id                    
way/26623782    NaN      NaN  
way/23979464    NaN      NaN  
way/290406242   NaN      NaN

In [7]:
features.explore(color="brown")

Plot the poster

In [8]:
import matplotlib.pyplot as plt
from utils import plot_poster

ax = plot_poster(features, CITY, COUNTRY)

plt.savefig("poster.png", facecolor="#ecedea", dpi=300)
plt.close()

<img src="poster.png" style="height: 900px; margin: auto" /> 

<div>
    <img src="assets/SRAI-diagram.png" class="srai-diagram"/>
</div>

## Regionalizers

* unify methods for dividing a given area into smaller regions. 
* based (mostly) on spatial indexes.

[API](https://kraina-ai.github.io/srai/latest/api/regionalizers/)<br>
[Examples](https://kraina-ai.github.io/srai/latest/examples/regionalizers/)

Types of regionalizers:

* H3Regionalizer
* S2Regionalizer
* VoronoiRegionalizer
* AdministativeBoundaryRegionalizer

### Spatial index regionalization

In [9]:
from srai.regionalizers import H3Regionalizer
from srai.plotting import plot_regions
from utils import CB_SAFE_PALLETE

In [10]:
regions = H3Regionalizer(resolution=9).transform(area)
plot_regions(regions, colormap=CB_SAFE_PALLETE)

### Data driven regionalization

In [11]:
from srai.loaders import OSMOnlineLoader

In [12]:
stops = OSMOnlineLoader().load(area, {"public_transport": "stop_position"})
stops.explore()

In [13]:
from srai.regionalizers import VoronoiRegionalizer
warnings.simplefilter("ignore")

regionalizer = VoronoiRegionalizer(seeds=stops)
regions = regionalizer.transform(area)

plot_regions(regions, colormap=CB_SAFE_PALLETE)

Generating regions: 100%|██████████| 570/570 [00:14<00:00, 40.63it/s]


### Administrative boundaries

In [14]:
from srai.regionalizers import AdministrativeBoundaryRegionalizer 

In [15]:
regionalizer = AdministrativeBoundaryRegionalizer(admin_level=9)
regions = regionalizer.transform(area)
plot_regions(regions, colormap=CB_SAFE_PALLETE)

Loading boundaries: 20it [00:00, 65.56it/s]


<div>
    <img src="assets/SRAI-diagram.png" class="srai-diagram"/>
</div>

## Embedders

Unify methods for mapping regions into a vector space.

[API](https://kraina-ai.github.io/srai/latest/api/embedders/)<br>
[Examples](https://kraina-ai.github.io/srai/latest/examples/embedders/)

Types of embedders:

* CountEmbedder
* ContextualCountEmbedder
* GTFS2VecEmbedder
* Hex2VecEmbedder
* Highway2VecEmbedder

### Simple embeddings

In [24]:
from srai.loaders import OSMPbfLoader
from srai.regionalizers import H3Regionalizer, geocode_to_region_gdf
from srai.loaders.osm_loaders.filters import HEX2VEC_FILTER

area = geocode_to_region_gdf(area_name)
features = OSMPbfLoader().load(area, HEX2VEC_FILTER)
regions = H3Regionalizer(resolution=9).transform(area)

[Basel, Basel-City, Switzerland] Counting pbf features: 636273it [00:01, 328439.30it/s]
[Basel, Basel-City, Switzerland] Parsing pbf file #1: 100%|██████████| 636273/636273 [00:22<00:00, 27685.66it/s]


In [25]:
from srai.joiners import IntersectionJoiner

joint = IntersectionJoiner().transform(regions, features)

In [26]:
from srai.embedders import CountEmbedder

embedder = CountEmbedder()
embeddings = embedder.transform(regions, features, joint)

embeddings.head(3)

aeroway_helipad  amenity_arts_centre  amenity_atm  \
region_id                                                            
891f8383337ffff                0                    0            0   
891f83830d3ffff                0                    0            0   
891f838108bffff                0                    0            0   

                 amenity_baby_hatch  amenity_bank  amenity_bar  amenity_bbq  \
region_id                                                                     
891f8383337ffff                   0             0            0            0   
891f83830d3ffff                   0             0            0            0   
891f838108bffff                   0             0            0            0   

                 amenity_bench  amenity_bicycle_parking  \
region_id                                                 
891f8383337ffff             14                        0   
891f83830d3ffff              0                        0   
891f838108bffff              0                        0   

                 amenity_bicycle_rental  ...  water_basin  water_canal  \
region_id                                ...                             
891f8383337ffff                       0  ...            0            0   
891f83830d3ffff                       0  ...            0            0   
891f838108bffff                       0  ...            0            0   

                 water_fish_pass  water_pond  water_river  waterway_canal  \
region_id                                                                   
891f8383337ffff                0           0            0               0   
891f83830d3ffff                0           0            0               0   
891f838108bffff                0           0            0               0   

                 waterway_ditch  waterway_river  waterway_stream  \
region_id                                                          
891f8383337ffff               0               0                2   
891f83830d3ffff               0               0                0   
891f838108bffff               0               0                0   

                 waterway_weir  
region_id                       
891f8383337ffff              0  
891f83830d3ffff              0  
891f838108bffff              0  

[3 rows x 369 columns]

In [29]:
from srai.plotting import plot_regions, plot_numeric_data

folium_map = plot_regions(area, colormap=["rgba(0,0,0,0.4)"], tiles_style="CartoDB positron")
plot_numeric_data(regions, embeddings, "amenity_bicycle_parking", map=folium_map)

## Questions?